In [41]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from collections import Counter
import gensim
from gensim.corpora.dictionary import Dictionary
from gensim.models.tfidfmodel import TfidfModel

# Load the data :

In [2]:
reviews=pd.read_csv(r"C:\Users\mohz2\Desktop\Awooda\reviewly\data\yelp_review.csv")
business=pd.read_csv(r"C:/Users/mohz2/Desktop/Awooda/reviewly/data/yelp_business.csv")
user=pd.read_csv(r"C:/Users/mohz2/Desktop/Awooda/reviewly/data/yelp_user.csv")

In [4]:
reviews.head(5)

review_id                 user_id             business_id  \
0  vkVSCC7xljjrAI4UGfnKEQ  bv2nCi5Qv5vroFiqKGopiw  AEx2SYEUJmTxVVB18LlCwA   
1  n6QzIUObkYshz4dz2QRJTw  bv2nCi5Qv5vroFiqKGopiw  VR6GpWIda3SfvPC-lg9H3w   
2  MV3CcKScW05u5LVfF6ok0g  bv2nCi5Qv5vroFiqKGopiw  CKC0-MOWMqoeWf6s-szl8g   
3  IXvOzsEMYtiJI0CARmj77Q  bv2nCi5Qv5vroFiqKGopiw  ACFtxLv8pGrrxMm6EgjreA   
4  L_9BTb55X0GDtThi6GlZ6w  bv2nCi5Qv5vroFiqKGopiw  s2I_Ni76bjJNK9yG60iD-Q   

   stars        date                                               text  \
0      5  2016-05-28  Super simple place but amazing nonetheless. It...   
1      5  2016-05-28  Small unassuming place that changes their menu...   
2      5  2016-05-28  Lester's is located in a beautiful neighborhoo...   
3      4  2016-05-28  Love coming here. Yes the place always needs t...   
4      4  2016-05-28  Had their chocolate almond croissant and it wa...   

   useful  funny  cool  
0       0      0     0  
1       0      0     0  
2       0      0     0  
3       0      0     0  
4       0      0     0

# One restaurant :

In [4]:
mon_ami_gabi = reviews[reviews["business_id"]=="4JNXUYY8wbaaDmk3BPzlWw"]

In [5]:
mon_ami_gabi.head()

review_id                 user_id             business_id  \
1720  YCzBgTYCyTtPAe2v8_GGKA  CZs1Eq7t1fqpXV1yox-CVg  4JNXUYY8wbaaDmk3BPzlWw   
2399  lPf1wwTu9VeWABHDPhu2tA  Zqk-ye_OHeH_sS1JsdsLgg  4JNXUYY8wbaaDmk3BPzlWw   
3430  voVb586hGvZC6vUA7HUIIw  RmThjWcv7x5Z_vVuOlRNwQ  4JNXUYY8wbaaDmk3BPzlWw   
7921  jipTZe7L20v422d2Di2_Tw  hBl_w9Rmn_Bz0HiMzwaknA  4JNXUYY8wbaaDmk3BPzlWw   
8793  D5r-QLswHpnxaMadQdi_dg  eZ5I1bHkdXoGOFKn_oOFFQ  4JNXUYY8wbaaDmk3BPzlWw   

      stars        date                                               text  \
1720      4  2017-10-25  Traditional French fare at the heart of the La...   
2399      5  2013-10-15  This is my go to place for the last 12 years, ...   
3430      2  2017-04-03  Mediocre food for too much money, at least at ...   
7921      4  2012-12-26  My family and I had dinner here and the wait w...   
8793      5  2015-10-21  Patio dining at its best. Steak au poive with ...   

      useful  funny  cool  
1720       0      0     1  
2399       4      0     2  
3430       0      0     0  
7921       0      0     0  
8793       0      0     0

In [6]:
mon_ami_gabi.count()

review_id      7362
user_id        7362
business_id    7362
stars          7362
date           7362
text           7362
useful         7362
funny          7362
cool           7362
dtype: int64

In [7]:
mon_ami_gabi_reviews = mon_ami_gabi[["text"]]

In [8]:
mon_ami_gabi_reviews.head(5)

text
1720  Traditional French fare at the heart of the La...
2399  This is my go to place for the last 12 years, ...
3430  Mediocre food for too much money, at least at ...
7921  My family and I had dinner here and the wait w...
8793  Patio dining at its best. Steak au poive with ...

# Text processing ...


Tokenization + lowercasing + alphabetical words + no stop words + lemmatization:

In [18]:
tokens = []
wordnet_lemmatizer = WordNetLemmatizer()
for lab, row in mon_ami_gabi_reviews.iterrows():
    token = word_tokenize(row["text"].lower())
    alpha_only = [t for t in token if t.isalpha()]
    no_stops = [t for t in alpha_only if t not in stopwords.words('english')]
    lemmatized = [wordnet_lemmatizer.lemmatize(t) for t in no_stops]
    tokens.append(lemmatized)
print(len(tokens))

7362


In [19]:
print(tokens[0])

['traditional', 'french', 'fare', 'heart', 'la', 'vega', 'strip', 'never', 'fails', 'satisfy', 'whether', 'regular', 'virgin', 'mon', 'ami', 'gabi', 'please', 'make', 'sure', 'save', 'room', 'dessert', 'perhaps', 'done', 'make', 'dining', 'experience', 'dessert', 'filled', 'table', 'made', 'scratch', 'sinfully', 'delicious', 'dessert', 'yes', 'sweet', 'seen', 'picture', 'dined', 'numerous', 'time', 'year', 'yes', 'food', 'dessert', 'onion', 'soup', 'steak', 'frites', 'mussel', 'mariniere', 'mussel', 'power', 'half', 'order', 'yes', 'half', 'clearly', 'utilize', 'doughy', 'stuff', 'scooping', 'white', 'wine', 'herb', 'broth', 'ca', 'go', 'wrong', 'pretty', 'much', 'anything', 'menu', 'offer', 'peruse', 'menu', 'order', 'away']


In [21]:
print(mon_ami_gabi_reviews.iloc[0]["text"])

Traditional French fare at the heart of the Las Vegas Strip that never fails to satisfy.  Whether you're a regular or virgin at Mon Ami Gabi please make sure you save room for dessert.  Perhaps do what I've done, just make the dining experience a dessert filled table;)  made from scratch and sinfully delicious desserts.  Yes, I have a sweet tooth- have you not seen my pictures!  
I've dined here numerous times over the years, yes Food and not only dessert.  
Onion soup, steak frites and those mussels mariniere! The mussels, I have will power and have the half order. Yes, half so I can clearly utilize that doughy stuff by scooping up the white wine & herbs broth:) 
You can't go wrong with pretty much anything the menu offers, so peruse that menu and order away!


# Filtering:

In [3]:
# City of Toronto
business = business[business['city'] == 'Toronto']


In [4]:
business.head()

business_id                      name        neighborhood  \
15  l09JfMeQ6ynYs5MCJtrcmQ          "Alize Catering"  Yonge and Eglinton   
20  lHYiCS-y8AFjUitv6MGpxg               "Starbucks"     Liberty Village   
24  VSGcuYDV3q-AAZ9ZPq4fBQ             "Sportster's"        The Danforth   
25  1K4qrnfyzKzGgJPBEcJaNQ  "Chula Taberna Mexicana"         Leslieville   
27  AtdXq_gu9NTE5rx4ct_dGg               "DAVIDsTEA"             Ryerson   

                    address     city state postal_code   latitude  longitude  \
15          "2459 Yonge St"  Toronto    ON     M4P 2H6  43.711399 -79.399339   
20        "85 Hanna Avenue"  Toronto    ON     M6K 3S3  43.639863 -79.419533   
24   "1430 Danforth Avenue"  Toronto    ON     M4J 1N4  43.682867 -79.326964   
25  "1058 Gerrard Street E"  Toronto    ON     M4M 3A6  43.669256 -79.335902   
27     "10 Dundas Street E"  Toronto    ON     M5B 2G9  43.656729 -79.380718   

    stars  review_count  is_open                                    categories  
15    3.0            12        0                    Italian;French;Restaurants  
20    4.0            21        1                             Food;Coffee & Tea  
24    2.5             7        1                    Bars;Sports Bars;Nightlife  
25    3.5            39        1  Tiki Bars;Nightlife;Mexican;Restaurants;Bars  
27    4.0             6        1                   Coffee & Tea;Food;Tea Rooms

In [6]:
# All the food categories:
business['categories'] = business['categories'].str.lower()

In [23]:
# selected_categories = ['restaurant', 'food', 'breakFast', 'pizza', 'burgers', 'diner', 'lunch', 'mexican', 'seafood', 'italian',
#                       'chinese', 'indian', 'korean', 'asian', 'sushi', 'brunch', 'cafe', 'thai', 'sandwich', 'bake', 'bagels']
selected_categories = ['restaurant']

In [24]:
# selecting all food businesses


In [25]:
food_businesses = pd.DataFrame(columns = list(business.columns.values))
for i in range(0,len(selected_categories)):
    df = business[business['categories'].str.contains(selected_categories[i])]
    food_businesses = food_businesses.append(df)
food_businesses = food_businesses.drop_duplicates()
food_businesses.shape

(7148, 13)

In [26]:
# only reviews about food:


In [27]:
food_reviews = reviews[reviews["business_id"].isin(food_businesses["business_id"])]

In [28]:
food_reviews.head()

review_id                 user_id             business_id  \
6   ymAUG8DZfQcFTBSOiaNN4w  u0LXt3Uea_GidxRW1xcsfg  9_CGhHMz8698M9-PkVf0CQ   
8   w41ZS9shepfO3uEyhXEWuQ  u0LXt3Uea_GidxRW1xcsfg  5r6-G9C4YLbC7Ziz57l3rQ   
10  PIsUSmvaUWB00qv5KTF1xA  u0LXt3Uea_GidxRW1xcsfg  z8oIoCT1cXz7gZP5GeU5OA   
11  PdZ_uFjbbkjtm3SCY_KrZw  u0LXt3Uea_GidxRW1xcsfg  XWTPNfskXoUL-Lf32wSk0Q   
13  lsoSqIrrDbQvWpMvsSj2xw  u0LXt3Uea_GidxRW1xcsfg  RtUvSWO_UZ8V3Wpj0n077w   

    stars        date                                               text  \
6       4  2012-05-11  Who would have guess that you would be able to...   
8       3  2013-02-09  Not bad!! Love that there is a gluten-free, ve...   
10      4  2013-05-01  This is currently my parents new favourite res...   
11      3  2011-09-28  Server was a little rude.\n\nOrdered the calam...   
13      3  2012-12-03  Wanted to check out this place due to all the ...   

    useful  funny  cool  
6        0      0     2  
8        1      0     0  
10       1      0     0  
11       5      0     1  
13       2      1     1

In [29]:
food_reviews.count()

review_id      303780
user_id        303780
business_id    303780
stars          303780
date           303780
text           303780
useful         303780
funny          303780
cool           303780
dtype: int64

# Selecting users with food reviews:

In [30]:
user_agg=food_reviews.groupby('user_id').agg({'review_id':['count']})

In [31]:
user_agg=user_agg.sort_values([('review_id','count')],ascending=False)

In [32]:
type(user_agg)

pandas.core.frame.DataFrame

In [33]:
user_agg.head(10)

review_id
                           count
user_id                         
CxDOIDnH8gp9KXzpBHJYXw       884
Q9mA60HnY87C1TW5kjAZ6Q       445
TbhyP24zYZqZ2VJZgu1wrg       401
0BBUmH7Krcax1RZgbH4fSA       361
FREeRQtjdJU83AFtdETBBw       350
1fNQRju9gmoCEvbPQBSo7w       334
tWBLn4k1M7PLBtAtwAg73g       316
yT_QCcnq-QGipWWuzIpvtw       302
V4TPbscN8JsFbEFiwOVBKw       296
O3pSxv1SyHpY4qi4Q16KzA       296

In [34]:
# users_ids = ["CxDOIDnH8gp9KXzpBHJYXw", "Tjv5bBtJ-Z_CLiY-rheG2g", "O3pSxv1SyHpY4qi4Q16KzA", "EGJXgD6YPieaUCQxfOdXbg",
#             "Q9mA60HnY87C1TW5kjAZ6Q", "veqfgg2AkKs_L70fx1Quag", "HFItzRohDHZvcKDrM6ABZg", "yT_QCcnq-QGipWWuzIpvtw",
#             "TbhyP24zYZqZ2VJZgu1wrg", "l0uKMipnY5z1aPltLWePOw"]

In [35]:
# users_ids = food_reviews.user_id.unique()
users_ids = list(user_agg.index.values) 


In [36]:
len(users_ids)

73041

In [37]:
users_ids[0]

'CxDOIDnH8gp9KXzpBHJYXw'

In [38]:
users_reviews = []
for i in users_ids:
    user_reviews = food_reviews[food_reviews["user_id"] == i]
    users_reviews.append(user_reviews)
    

In [39]:
len(users_reviews)

73041

# NLP:

In [40]:
users_dictionaries = []
for i in users_reviews:
    user_dictionary = []
    wordnet_lemmatizer = WordNetLemmatizer()
    for lab, row in i.iterrows():
        token = word_tokenize(row["text"].lower())
        alpha_only = [t for t in token if t.isalpha()]
        no_stops = [t for t in alpha_only if t not in stopwords.words('english')]
        lemmatized = [wordnet_lemmatizer.lemmatize(t) for t in no_stops]
        for t in lemmatized:
            user_dictionary.append(t)
    users_dictionaries.append(user_dictionary)

In [42]:
len(users_dictionaries)

73041

In [20]:
# users_dictionaries[0]

# Tf-idf:

In [49]:
# first we create one doc to contain the tokens of both users
users_dictionaries

[['wanting',
  'try',
  'seven',
  'life',
  'taco',
  'since',
  'opened',
  'never',
  'lucky',
  'either',
  'downtown',
  'day',
  'closed',
  'one',
  'time',
  'wednesday',
  'supposed',
  'open',
  'closed',
  'renovation',
  'finally',
  'made',
  'upset',
  'stomach',
  'fried',
  'chicken',
  'ate',
  'earlier',
  'brunch',
  'admired',
  'blackened',
  'mahi',
  'mahi',
  'taco',
  'friend',
  'ordered',
  'looked',
  'delicious',
  'sadly',
  'stomach',
  'turning',
  'torillas',
  'looked',
  'soft',
  'chewy',
  'fish',
  'grilled',
  'without',
  'heavy',
  'batter',
  'way',
  'liked',
  'mine',
  'guess',
  'needed',
  'come',
  'back',
  'next',
  'time',
  'kensington',
  'market',
  'promised',
  'watched',
  'friend',
  'ate',
  'taco',
  'nova',
  'era',
  'bakery',
  'cantinho',
  'bakery',
  'vannis',
  'ristorante',
  'e',
  'b',
  'e',
  'r',
  'vannis',
  'ristorante',
  'third',
  'stop',
  'november',
  'crawl',
  'brunch',
  'time',
  'good',
  'time',
  '

In [50]:
len(users_dictionaries)

10349

In [43]:
# Now we create a dictionary - mapping with ID for each token :
dictionary = Dictionary(users_dictionaries)

In [58]:
dictionary.token2id

{'aaa': 0,
 'abalone': 1,
 'abc': 2,
 'aberdeen': 3,
 'ability': 4,
 'able': 5,
 'abruzzo': 6,
 'abt': 7,
 'aburi': 8,
 'abv': 9,
 'ac': 10,
 'acadia': 11,
 'accent': 12,
 'accented': 13,
 'accept': 14,
 'accepts': 15,
 'access': 16,
 'accessible': 17,
 'accidentally': 18,
 'accommodate': 19,
 'accommodating': 20,
 'accompanied': 21,
 'accomplish': 22,
 'according': 23,
 'accordingly': 24,
 'accustom': 25,
 'ace': 26,
 'aceitunas': 27,
 'achieve': 28,
 'achiote': 29,
 'achovies': 30,
 'ackee': 31,
 'acknowledged': 32,
 'acknowledgement': 33,
 'acknowledging': 34,
 'acme': 35,
 'acoustic': 36,
 'acquired': 37,
 'across': 38,
 'act': 39,
 'action': 40,
 'actual': 41,
 'actually': 42,
 'ad': 43,
 'adam': 44,
 'adamson': 45,
 'adapt': 46,
 'adaptation': 47,
 'adapted': 48,
 'add': 49,
 'added': 50,
 'addictive': 51,
 'adding': 52,
 'addition': 53,
 'additional': 54,
 'address': 55,
 'addressing': 56,
 'adega': 57,
 'adequate': 58,
 'adjust': 59,
 'adjusted': 60,
 'admin': 61,
 'admire': 62

In [44]:
# Using the dictionary we can then create a corpus :
corpus = [dictionary.doc2bow(doc) for doc in users_dictionaries]

In [45]:
# Each tuple contains a token id and frequency of each token in the document.
# print(corpus)

In [46]:
# Then we build our Tf-idf model: here each tuple contain token id and weight.
tfidf = TfidfModel(corpus)

In [47]:
print(tfidf)

TfidfModel(num_docs=73041, num_nnz=9622778)


In [48]:
# Now we will create a similarity measure object in tf-idf space:
sims = gensim.similarities.Similarity(r'C:\Users\mohz2\Desktop\Awooda\reviewly',tfidf[corpus],num_features=len(dictionary))

In [58]:
print(sims)
print(type(sims))

Similarity index with 10349 documents in 0 shards (stored under C:\Users\mohz2\Desktop\Awooda\reviewly)
<class 'gensim.similarities.docsim.Similarity'>


In [60]:
# lets consider the dict of the user with most reviews as query document :
user_A_bow = dictionary.doc2bow(users_dictionaries[0])

In [93]:
# print(user_A_bow)

In [62]:
# use the tfidf model to find the weights of tokens in user_A_bow:
user_A_tfidf = tfidf[user_A_bow]

In [63]:
print(user_A_tfidf)

[(0, 0.01734108261791476), (1, 0.02523854620912547), (2, 0.01066916070698082), (3, 0.013166224943752875), (4, 0.019198285596745), (5, 0.010782590450057979), (6, 0.022870691967059327), (7, 0.036223782995803366), (8, 0.01085600264577369), (9, 0.012033231800323617), (10, 0.019969094476731925), (11, 0.029023037629386492), (12, 0.01156792173701969), (13, 0.04273231833032288), (14, 0.01860039977995105), (15, 0.016040223886892108), (16, 0.02139414228386718), (17, 0.02141715500175217), (18, 0.010918604464033145), (19, 0.02805664979605982), (20, 0.016254688519071442), (21, 0.018930235224273995), (22, 0.024755692624207747), (23, 0.0187131613591101), (24, 0.0072947456576625165), (25, 0.010468614950401387), (26, 0.023796217008847917), (27, 0.010711136148128683), (28, 0.02476989453323572), (29, 0.011529368877241685), (30, 0.056232420900656686), (31, 0.038966860150543674), (32, 0.007829355313331933), (33, 0.019969094476731925), (34, 0.019969094476731925), (35, 0.023174816409857628), (36, 0.014488011

# Computing similarity:

In [65]:
# Now we compare user_A_dictionary with the 10 docs in our tfidf model:
user_A_similarity=sims[user_A_tfidf]

In [66]:
len(user_A_similarity)

10349

In [67]:
user_A_similarity[0:10]

array([0.9999995 , 0.39210668, 0.16340385, 0.27195433, 0.2885411 ,
       0.28728876, 0.38943887, 0.24332349, 0.29746738, 0.33056784],
      dtype=float32)

In [80]:
sorted(user_A_similarity,reverse=True)

[0.9999995,
 0.422702,
 0.3985967,
 0.39210668,
 0.38943887,
 0.38171682,
 0.37621182,
 0.37383947,
 0.3736481,
 0.36556733,
 0.3555594,
 0.35382476,
 0.3522187,
 0.35002875,
 0.3498075,
 0.3464888,
 0.3439089,
 0.34252134,
 0.3416919,
 0.34080273,
 0.3391327,
 0.33808494,
 0.33521515,
 0.33373174,
 0.3308047,
 0.33065417,
 0.33056784,
 0.3304523,
 0.3298074,
 0.32733363,
 0.32553205,
 0.32460976,
 0.3244524,
 0.3243777,
 0.3240188,
 0.323963,
 0.32338017,
 0.32327738,
 0.32270384,
 0.32117525,
 0.3197274,
 0.31920302,
 0.3190013,
 0.31707093,
 0.31548718,
 0.31418312,
 0.31297526,
 0.31195065,
 0.31165487,
 0.3114714,
 0.31114897,
 0.31096804,
 0.3109151,
 0.3102892,
 0.30940327,
 0.3092988,
 0.3090583,
 0.30889997,
 0.30742997,
 0.30629626,
 0.30605203,
 0.30539834,
 0.3046126,
 0.30438724,
 0.303917,
 0.30213106,
 0.30057192,
 0.30044726,
 0.29978418,
 0.29950264,
 0.2984505,
 0.29770347,
 0.2976798,
 0.29746738,
 0.29745248,
 0.2964223,
 0.29522076,
 0.29498264,
 0.29490456,
 0.294

In [81]:
# consider the second user dictionary as a query doc:
user_B_bow = dictionary.doc2bow(users_dictionaries[1])
user_B_tfidf = tfidf[user_B_bow]
user_B_similarity=sims[user_B_tfidf]
user_B_similarity[0:10]

array([0.39210668, 0.9999998 , 0.18840143, 0.25711763, 0.29917574,
       0.3260107 , 0.40674904, 0.2361319 , 0.31612846, 0.3665878 ],
      dtype=float32)

In [82]:
sorted(user_B_similarity,reverse=True)

[0.9999998,
 0.470542,
 0.45059595,
 0.43490118,
 0.42014986,
 0.40959883,
 0.40674904,
 0.40420112,
 0.39210668,
 0.38518846,
 0.38505,
 0.38062268,
 0.37839058,
 0.3720014,
 0.36923286,
 0.3665878,
 0.36654153,
 0.36421052,
 0.36417532,
 0.36265698,
 0.36120227,
 0.3608573,
 0.36052278,
 0.35948148,
 0.3570041,
 0.35660008,
 0.3565805,
 0.35555217,
 0.35401252,
 0.35374063,
 0.35280547,
 0.34952474,
 0.3478244,
 0.3463838,
 0.34310102,
 0.34172192,
 0.34097546,
 0.34064445,
 0.33917817,
 0.33864802,
 0.336333,
 0.33532327,
 0.3342225,
 0.33390844,
 0.3328707,
 0.33180147,
 0.33172628,
 0.33162552,
 0.33096793,
 0.32984287,
 0.32949975,
 0.3293317,
 0.32927483,
 0.32807663,
 0.3275018,
 0.32712767,
 0.32684135,
 0.32629043,
 0.3260107,
 0.32574984,
 0.3255489,
 0.32531214,
 0.3244153,
 0.32355958,
 0.32204974,
 0.32188186,
 0.32168865,
 0.319358,
 0.31916186,
 0.3176936,
 0.31724396,
 0.31679338,
 0.31673822,
 0.31612846,
 0.3155908,
 0.31548035,
 0.31406438,
 0.3131296,
 0.3129304,
 

# Similarity for 100 users: 

In [49]:
users_similarities=[]
for doc in corpus[0:100] : 
    indices = []
    user_tfidf = tfidf[doc]
    user_similarity=sims[user_tfidf]
    ordered = sorted(user_similarity,reverse=True)
    for i in ordered[1:11]:
        index = user_similarity.tolist().index(i)
        indices.append(index)
    # the 10 most similar users to user A are:
    similar_users=[]
    for i in indices:
        similar_users.append(users_ids[i])
    users_similarities.append(similar_users)

In [50]:
len(users_similarities)

100

In [51]:
users_similarities[0]

['Wu0yySWcHQ5tZ_59HNiamg',
 '0BBUmH7Krcax1RZgbH4fSA',
 '8HCEPF0IflyB690Q745fKg',
 'rGd8YUtvhSdMm8-9cMdQ4Q',
 'm7z-tX6XDZ27xGhGjnI21w',
 'KBh4r16e9Grc1HI9pG4wTg',
 'DNlzbI54zCOa4to-vTWBJQ',
 'TbhyP24zYZqZ2VJZgu1wrg',
 'Kj9cFO70zZOQorN0mgeLWA',
 'mrru6hbeQLvagU4vkfuqmw']

# Dataframe for 100 users similarities:

In [55]:
d = {"user_id": users_ids[0:100], "similar_users": users_similarities}

In [56]:
similarities = pd.DataFrame(data=d)

In [59]:
similarities.head(10)

user_id                                      similar_users
0  CxDOIDnH8gp9KXzpBHJYXw  [Wu0yySWcHQ5tZ_59HNiamg, 0BBUmH7Krcax1RZgbH4fS...
1  Q9mA60HnY87C1TW5kjAZ6Q  [_t3BJzyGaqr9mcDazYiYAQ, TbhyP24zYZqZ2VJZgu1wr...
2  TbhyP24zYZqZ2VJZgu1wrg  [0BBUmH7Krcax1RZgbH4fSA, alUuOskFSl1bODjnce2Pp...
3  0BBUmH7Krcax1RZgbH4fSA  [uHZr3XbjKvRTwdXLXrFuvg, alUuOskFSl1bODjnce2Pp...
4  FREeRQtjdJU83AFtdETBBw  [Kj9cFO70zZOQorN0mgeLWA, uSMK7y_H2DzRX7WcKXtFg...
5  1fNQRju9gmoCEvbPQBSo7w  [TbhyP24zYZqZ2VJZgu1wrg, 0BBUmH7Krcax1RZgbH4fS...
6  tWBLn4k1M7PLBtAtwAg73g  [TbhyP24zYZqZ2VJZgu1wrg, 65yB0ydGXOZ_-T6J_GbKf...
7  yT_QCcnq-QGipWWuzIpvtw  [GERRIWMslcP4-O6mLErPSQ, 0BBUmH7Krcax1RZgbH4fS...
8  V4TPbscN8JsFbEFiwOVBKw  [Kj9cFO70zZOQorN0mgeLWA, TbhyP24zYZqZ2VJZgu1wr...
9  O3pSxv1SyHpY4qi4Q16KzA  [9r8icFWxG8wwdbVADDhMvQ, ait2YjzBn3CIoc_-wU-l6...